In [23]:
# Imports
import json
import os
import re
import textwrap
import warnings
from pathlib import Path

import matplotlib.pyplot as plt
import numpy as np  # linear algebra
import pandas as pd  # data processing, CSV file I/O (e.g. pd.read_csv)
import plotly.express as px
import rich
import seaborn as sns
import seaborn.objects as so
from sklearn import preprocessing

warnings.filterwarnings('ignore')

dataset_path = Path('../data/')
for file in dataset_path.iterdir():
    if file.suffix == '.csv':
        df = pd.read_csv(file)
        print(file)

..\data\State_of_data_BR_2023_Kaggle - df_survey_2023.csv


In [24]:
def load_json(file_path: Path) -> dict:
    with open(file_path, 'r', encoding="utf-8") as file:
        return json.load(file)
    
def save_json(file_path: Path, data: dict) -> None:
    with open(file_path, 'w') as file:
        json.dump(data, file, ensure_ascii=False ,indent=4)

# Load the merged question
merged_json_path = Path("../questions_jsons/completions_good_features.json")
questions_merged_dict = load_json(merged_json_path)

for i, question in enumerate(questions_merged_dict.values()):
    if i == 3:
        break
    print(f"{i + 1}. {question['question']}\n")

1. Idade

2. Genero

3. Cor/raca/etnia



In [25]:
# criando um dicionário com o número da pergunta e qual é a pergunta
column_dict = {}

for col in df.columns:

    match = re.match(r"\('(.+?)', '(.+?)'\)", col)
    if match:
        cod, pergunta = match.groups()
        column_dict[cod.replace(" ", "")] = pergunta
    else:
        print(col)

# print(column_dict)

('P6_b_16 ', 'SQL Server Integration Services (SSIS))


In [26]:
column_dict['P6_b_16']='SQL Server Integration Services (SSIS)'

In [27]:
df_treat = df.copy()
df_treat.columns = list(column_dict.keys())

In [28]:
# rename wrong column
df_treat.rename(columns={'P7_1': 'P7_a'}, inplace=True)
df_treat.rename(columns={'P8_3': 'P8_c'}, inplace=True)

# Switch two columns that were in the wrong order
df_treat.rename(columns={'P7_a': 'P7_a_1', 'P7_a_1': 'P7_a'}, inplace=True) # P7_a_1 (antiga P7_a), has corrupted data
df_treat.rename(columns={'P8_b': 'P8_b_1', 'P8_b_1': 'P8_b'}, inplace=True) 
df_treat.rename(columns={'P8_c': 'P8_c_1', 'P8_c_1': 'P8_c'}, inplace=True) 
df_treat.rename(columns={'P4_a_1': 'P4_a2'}, inplace=True) # P4_a_1 Is not an alternative for P4_a 

# Remove columns
#df_treat.drop(columns=[''], inplace=True) 

# Create new dummy columns with 0 on all rows
#df_treat[''] = 0

# Add columns to dictionary

In [29]:
df_treat["P4_a"].value_counts()

P4_a
*Análise de Dados/BI:* Extrai e cruza dados unindo diferentes fontes da informação; analisa dados visando identificar padrões, gerar insights e levantar perguntas; desenvolve dashboards, relatórios e visualizações de dados em ferramentas de BI.     1795
*Engenharia de Dados:* Modela soluções de arquitetura de dados; define modelagens de repositórios de dados (Data Lake, Data Warehouse, Data Lakehouse); desenvolve estratégias de aquisição de dados, recuperação de informação e pipelines de dados.     912
*Ciência de Dados/Machine Learning/AI: *Desenha e executa experimentos com o objetivo de responder perguntas do negócio; desenvolve modelos preditivos e algoritmos de Machine Learning com o objetivo de otimizar e automatizar a tomada de decisão.     748
Não atuo em nenhuma das frentes citadas.                                                                                                                                                                                                 

In [30]:
column = "P4_a"
df_treat_not_null = df_treat[df_treat[column].notnull()]
df_treat_not_null[column].iloc[0]

# df_treat_not_null[["P7_a","P7_a_1","P7_a_2","P7_a_3","P7_a_4","P7_a_5","P7_a_6","P7_a_7","P7_a_8","P7_a_9","P7_a_10"]]

'*Ciência de Dados/Machine Learning/AI: *Desenha e executa experimentos com o objetivo de responder perguntas do negócio; desenvolve modelos preditivos e algoritmos de Machine Learning com o objetivo de otimizar e automatizar a tomada de decisão.'

In [31]:
# Manual Analysis
columns_to_maintain = ["P1_l", "P1_m", "P2_i", "P2_j", "P3_c",
                    "P4_a", # Mas não a P4_a_1
                "P4_b", "P4_c", "P4_d", "P4_e", "P4_g", "P4_j", "P5_b", "P6_a", "P6_b", "P6_g", "P6_h", "P7_a", "P7_b", "P7_d", "P8_a", "P8_b", "P8_c", "P8_d"
                    ]

column_in_doubt = [
    "P2_b", "P2_d", "P2_e", "P2_f", "P2_g", # Dados de emprego atuais da pessoa (cargo, se é gerente, setor, etc.)
    "P2_o", # Critérios que a pessoa acha importante ao escolher uma vaga de emprego (salário, clima, desenvolvimento, etc.)
    "P2_r", # Modelo de trabalho atual da pessoa (remoto, presencial, híbrido). Estou mais para o não
    "P6_c", "P6_d", "P6_e", "P6_f" # Se a empresa que trabalha tem data lake, data warehouse, etc.
    ]

possible_for_ordering = ["P1_l", "P2_e", "P2_g", "P2_i", "P2_j", "P2_r"]

target = "P2_h"

# For now, use both columns_to_maintain and column_in_doubt
# categorical columns and numerical columns
# colunas categóricas
cat_cols = [col for col in df_treat.columns if df_treat[col].dtype=='O' and col in (columns_to_maintain + column_in_doubt)]

# colunas numéricas
num_cols = [col for col in df_treat.columns if (df_treat[col].dtype=='int64' or df_treat[col].dtype=='float64') and col in (columns_to_maintain + column_in_doubt)]

merged_questions = load_json(Path("../questions_jsons/merged_questions.json"))
# Flatten the merged_questions dictionary to remove part divisions
merged_questions_no_part_division = {
    question['col_id']: question
    for part in merged_questions.values()
    for question in part
}


cat_cols_with_alternatives = [cat_col for cat_col in cat_cols if "possiveis_respostas" in merged_questions_no_part_division[cat_col]]

cat_cols_without_alternatives = sorted(set(cat_cols) - set(cat_cols_with_alternatives))

rich.print(f"Categorical columns: {sorted(cat_cols)}")
rich.print(f"Categorical columns with alternatives: {sorted(cat_cols_with_alternatives)}")
rich.print(f"Categorical columns without alternatives: {cat_cols_without_alternatives}")
rich.print(f"Numerical columns: {sorted(num_cols)}")

Categorical columns: ['P1_l', 'P1_m', 'P2_b', 'P2_e', 'P2_f', 'P2_g', 'P2_i', 'P2_j', 'P2_o', 'P2_r', 'P3_c', 
'P4_a', 'P4_b', 'P4_c', 'P4_d', 'P4_e', 'P4_g', 'P4_j', 'P5_b', 'P6_a', 'P6_b', 'P6_e', 'P6_g', 'P6_h', 'P7_a', 
'P8_b', 'P8_c']

Categorical columns with alternatives: ['P2_o', 'P3_c', 'P4_a', 'P4_b', 'P4_c', 'P4_d', 'P4_g', 'P4_j', 'P6_a', 
'P6_b', 'P6_h', 'P7_a', 'P8_b', 'P8_c']

Categorical columns without alternatives: ['P1_l', 'P1_m', 'P2_b', 'P2_e', 'P2_f', 'P2_g', 'P2_i', 'P2_j', 'P2_r', 
'P4_e', 'P5_b', 'P6_e', 'P6_g']

Numerical columns: ['P2_d', 'P6_c', 'P6_d', 'P6_f', 'P7_b', 'P7_d', 'P8_a', 'P8_d']

In [32]:
# See the the most common values in the column
counter = 0
for row in df_treat["P3_c"]:
    if counter == 10:
        break
    print(row)
    counter += 1

nan
nan
nan
nan
nan
nan
nan
Sou gestor da equipe responsável pela engenharia de dados e por manter o Data Lake da empresa como fonte única dos dados, garantindo a qualidade e confiabilidade da informação.
nan
nan


In [33]:
# print col P2_o at index 901
print(df_treat["P2_o"].iloc[901])
print(df_treat["P2_o_1"].iloc[901])
print(df_treat["P2_o(list)"].iloc[901])

# print entire row at index 901
print(df_treat.iloc[901])

sasasaas
0.0


KeyError: 'P2_o(list)'

In [36]:
# It's better to not depend on the numerical values of the questions that have multiple answers. So try to create new columns based on the parent columns

# Create new columns first
for col in cat_cols_with_alternatives:
    df_treat[col + "(list)"] = df_treat.apply(lambda _: [], axis=1)

for col in cat_cols_with_alternatives:
    normalized_alternatives = []
    for alternative_name, alternative_answer in merged_questions_no_part_division[col]["possiveis_respostas"].items():
        # regex for leaving only alphanumeric characters, accented characters and spaces
        normalized_alternatives.append(re.sub(r"[^0-9a-záàâãéèêíïóôõöúçñ\n +]", " ", alternative_answer.lower()).rstrip())
        # rich.print(f"{alternative_answer} -> {normalized_alternatives[-1]}")
    # each parent column has on its rows a string of answers that are the normalized_alternatives divided by ",". But the answers also might have a "," on them, so a split(",") wont work and a comparison with normalized_alternatives will need to happen. So try to split them and create a new column that has the list of answers
    for index, row in df_treat.iterrows():
        try:
            if pd.notna(row[col]):
                normalized_answers = re.sub(r"[^0-9a-záàâãéèêíïóôõöúçñ\n+]", " ", row[col].lower())
                df_treat.at[index, col + "(list)"] = [normalized_alternative for normalized_alternative in normalized_alternatives if normalized_alternative in normalized_answers]
                # Count difference in length between the original string and the list of answers to see if there are any answers that were not found
                if len(normalized_answers) != len("  ".join(df_treat.at[index, col + "(list)"])):
                    # if len from the list of answers is 0, then probably the person only responded the "outros" option, so deal with it
                    if len("  ".join(df_treat.at[index, col + "(list)"])) == 0:
                        # Remove the "outros" option from the answers
                        df_treat.at[index, col + "(list)"] = []
                        # or remove the entire row from the dataframe
                        # df_treat.drop(index, inplace=True)

                    # if difference in length is very big, print the values to see what is happening
                    if abs(len(normalized_answers) - len("  ".join(df_treat.at[index, col + "(list)"])) > 400): 
                        rich.print(f"col {col} at index {index}")
                        # rich.print(f"Original answer: {row[col]}")
                        # rich.print(f"Normalized answer: {normalized_answers}")
                        rich.print(f"Answers found: {df_treat.at[index, col + "(list)"]}")
                        # rich.print(f"Answers found (str): {"  ".join(df_treat.at[index, col + "(list)"])}")
                        rich.print(len(normalized_answers), " | ", len("  ".join(df_treat.at[index, col + "(list)"])))
            else:
                df_treat.at[index, col + "(list)"] = []
        except Exception as e:
            rich.print(f"Error on column {col} at index {index}")
            rich.print(f"Value being set: {df_treat.at[index, col + "(list)"]}")
            raise e

col P3_c at index 262

Original answer: Pensar na visão de longo prazo de dados da empresa e fortalecimento da cultura analítica da 
companhia., Organização de treinamentos e iniciativas com o objetivo de aumentar a maturidade analítica das áreas 
de negócios., Atração, seleção e contratação de talentos para o time de dados., Decisão sobre contratação de 
ferramentas e tecnologias relacionadas a dados., Sou gestor da equipe responsável pela engenharia de dados e por 
manter o Data Lake da empresa como fonte única dos dados, garantindo a qualidade e confiabilidade da informação., 
Sou gestor da equipe responsável pela entrega de dados, estudos, relatórios e dashboards para as áreas de negócio 
da empresa., Sou gestor da equipe responsável por iniciativas e projetos envolvendo Inteligência Artificial e 
Machine Learning., Apesar de ser gestor ainda atuo na parte técnica, construindo soluções/análises/modelos etc., 
Gestão de projetos de dados, cuidando das etapas, equipes envolvidas, atingimento dos objetivos etc., Gestão de 
produtos de dados, cuidando da visão dos produtos, backlog, feedback de usuários etc., Gestão de pessoas, apoio no 
desenvolvimento das pessoas, evolução de carreira,, Operação da equipe de dados, criação de produtos e suporte a 
novos cientistas e pessoas engenheiras.

Normalized answer: pensar na visão de longo prazo de dados da empresa e fortalecimento da cultura analítica da 
companhia   organização de treinamentos e iniciativas com o objetivo de aumentar a maturidade analítica das áreas 
de negócios   atração  seleção e contratação de talentos para o time de dados   decisão sobre contratação de 
ferramentas e tecnologias relacionadas a dados   sou gestor da equipe responsável pela engenharia de dados e por 
manter o data lake da empresa como fonte única dos dados  garantindo a qualidade e confiabilidade da informação   
sou gestor da equipe responsável pela entrega de dados  estudos  relatórios e dashboards para as áreas de negócio 
da empresa   sou gestor da equipe responsável por iniciativas e projetos envolvendo inteligência artificial e 
machine learning   apesar de ser gestor ainda atuo na parte técnica  construindo soluções análises modelos etc   
gestão de projetos de dados  cuidando das etapas  equipes envolvidas  atingimento dos objetivos etc   gestão de 
produtos de dados  cuidando da visão dos produtos  backlog  feedback de usuários etc   gestão de pessoas  apoio no 
desenvolvimento das pessoas  evolução de carreira   operação da equipe de dados  criação de produtos e suporte a 
novos cientistas e pessoas engenheiras

Answers found: ['pensar na visão de longo prazo de dados da empresa e fortalecimento da cultura analítica da 
companhia', 'organização de treinamentos e iniciativas com o objetivo de aumentar a maturidade analítica das áreas 
de negócios', 'atração  seleção e contratação de talentos para o time de dados', 'decisão sobre contratação de 
ferramentas e tecnologias relacionadas a dados', 'sou gestor da equipe responsável pela engenharia de dados e por 
manter o data lake da empresa como fonte única dos dados  garantindo a qualidade e confiabilidade da informação', 
'sou gestor da equipe responsável pela entrega de dados  estudos  relatórios e dashboards para as áreas de negócio 
da empresa', 'sou gestor da equipe responsável por iniciativas e projetos envolvendo inteligência artificial e 
machine learning', 'apesar de ser gestor ainda atuo na parte técnica  construindo soluções análises modelos etc', 
'gestão de projetos de dados  cuidando das etapas  equipes envolvidas  atingimento dos objetivos etc', 'gestão de 
produtos de dados  cuidando da visão dos produtos  backlog  feedback de usuários etc', 'gestão de pessoas  apoio no
desenvolvimento das pessoas  evolução de carreira']

Answers found (str): pensar na visão de longo prazo de dados da empresa e fortalecimento da cultura analítica da 
companhia  organização de treinamentos e iniciativas com o objetivo de aumentar a maturidade analítica das áreas de
negócios  atração  seleção e contratação de talentos para o time de dados  decisão sobre contratação de ferramentas
e tecnologias relacionadas a dados  sou gestor da equipe responsável pela engenharia de dados e por manter o data 
lake da empresa como fonte única dos dados  garantindo a qualidade e confiabilidade da informação  sou gestor da 
equipe responsável pela entrega de dados  estudos  relatórios e dashboards para as áreas de negócio da empresa  sou
gestor da equipe responsável por iniciativas e projetos envolvendo inteligência artificial e machine learning  
apesar de ser gestor ainda atuo na parte técnica  construindo soluções análises modelos etc  gestão de projetos de 
dados  cuidando das etapas  equipes envolvidas  atingimento dos objetivos etc  gestão de produtos de dados  
cuidando da visão dos produtos  backlog  feedback de usuários etc  gestão de pessoas  apoio no desenvolvimento das 
pessoas  evolução de carreira

...

Answers found: []

Answers found (str):

244  |  0

col P4_a at index 2125

KeyboardInterrupt: 

In [24]:
# Print colummns that have "_list" in their name
df_treat[[col for col in df_treat.columns if "_list" in col]]

P2_o_list  \
0     [remuneração salário, flexibilidade de trabalh...   
1     [remuneração salário, benefícios, flexibilidad...   
2     [remuneração salário, flexibilidade de trabalh...   
3                                                    []   
4     [remuneração salário, flexibilidade de trabalh...   
...                                                 ...   
5288  [flexibilidade de trabalho remoto, oportunidad...   
5289  [flexibilidade de trabalho remoto, ambiente e ...   
5290  [remuneração salário, oportunidade de aprendiz...   
5291                                                 []   
5292                                                 []   

                                              P3_c_list P4_a_list  \
0                                                    []        []   
1                                                    []        []   
2                                                    []        []   
3                                                    []        []   
4                                                    []        []   
...                                                 ...       ...   
5288  [pensar na visão de longo prazo de dados da em...        []   
5289                                                 []        []   
5290                                                 []        []   
5291                                                 []        []   
5292                                                 []        []   

                                              P4_b_list  \
0     [dados relacionais  estruturados em bancos sql...   
1     [dados relacionais  estruturados em bancos sql...   
2     [dados relacionais  estruturados em bancos sql...   
3                                                    []   
4     [dados relacionais  estruturados em bancos sql...   
...                                                 ...   
5288                                                 []   
5289  [dados relacionais  estruturados em bancos sql...   
5290  [dados relacionais  estruturados em bancos sql...   
5291                                                 []   
5292                                                 []   

                                              P4_c_list  \
0     [dados relacionais  estruturados em bancos sql...   
1       [dados relacionais  estruturados em bancos sql]   
2     [dados relacionais  estruturados em bancos sql...   
3                                                    []   
4     [dados relacionais  estruturados em bancos sql...   
...                                                 ...   
5288                                                 []   
5289  [dados relacionais  estruturados em bancos sql...   
5290  [dados relacionais  estruturados em bancos sql...   
5291                                                 []   
5292                                                 []   

                     P4_d_list                              P4_g_list  \
0                [sql, python]  [sql server, s3, sqlite, redis, hive]   
1                [sql, python]                                   [s3]   
2     [sql, python, sas stata]              [s3, amazon athena, hive]   
3                           []                                     []   
4                [sql, python]           [google bigquery, snowflake]   
...                        ...                                    ...   
5288                        []                                     []   
5289             [sql, python]                      [google bigquery]   
5290             [sql, python]           [mongodb, s3, amazon athena]   
5291                        []                                     []   
5292                        []                                     []   

                                              P4_j_list P6_a_list P6_b_list  \
0     [não utilizo nenhuma ferramenta de bi no traba...        []        []   
1                           [microsoft powerbi, looker]